In [503]:
# Import libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from datetime import datetime

# Show all columns
pd.set_option('display.max_rows', None)

In [572]:
# Import banking data
# Note: This data was extracted on 1996

# Each record describes characteristics of a client
client = pd.read_csv('./data/raw/data_berka/client.asc', sep=';')

# Each record describes static characteristics of an account
account = pd.read_csv('./data/raw/data_berka/account.asc', sep=';')

# Each record describes a credit card issued to an account
card = pd.read_csv('./data/raw/data_berka/card.asc', sep=';')

# Each record describes demographic characteristics of a district
district = pd.read_csv('./data/raw/data_berka/district.asc', sep=';')

# Each record relates together a client with an account
# i.e. this relation describes the rights of clients to operate accounts
disp = pd.read_csv('./data/raw/data_berka/disp.asc', sep=';')

# Each record describes characteristics of a payment order (debits only)
order = pd.read_csv('./data/raw/data_berka/order.asc', sep=';')

# Each record describes one transaction on an account
trans = pd.read_csv('./data/raw/data_berka/trans.asc', sep=';', low_memory=False)

# Each record describes a loan granted for a given account
loan = pd.read_csv('./data/raw/data_berka/loan.asc', sep=';')

In [463]:
client.head()

client_id  birth_number  district_id
0          1        706213           18
1          2        450204            1
2          3        406009            1
3          4        561201            5
4          5        605703            5

In [489]:
client.isna().sum().sum()

0

In [490]:
client['birth year'] = client['birth_number'].astype(str).str[0:2].astype(int)+ 1900
client['birth month'] = client['birth_number'].astype(str).str[2:4].astype(int)
client['birth day'] = client['birth_number'].astype(str).str[4:6].astype(int)
client['gender'] = 'M'
client.loc[client['birth month']>50, 'gender'] = 'F'
client.loc[client['birth month']>50, 'birth month'] = client['birth month'] - 50
client['age'] = 1996 - client['birth year'] 
client['age_group'] = client['age']//10*10

client['birth date'] = client.apply(lambda a: datetime(a['birth year'], a['birth month'], a['birth day']), axis = 1)
client.head()

client_id  birth_number  district_id  birth year  birth month  birth day  \
0          1        706213           18        1970           12         13   
1          2        450204            1        1945            2          4   
2          3        406009            1        1940           10          9   
3          4        561201            5        1956           12          1   
4          5        605703            5        1960            7          3   

  gender  age  age_group birth date  
0      F   27         20 1970-12-13  
1      M   52         50 1945-02-04  
2      F   57         50 1940-10-09  
3      M   41         40 1956-12-01  
4      F   37         30 1960-07-03

In [491]:
del client['birth_number'], client['birth month'], client['birth day'], client['birth year']

In [492]:
client

client_id  district_id gender  age  age_group birth date
0             1           18      F   27         20 1970-12-13
1             2            1      M   52         50 1945-02-04
2             3            1      F   57         50 1940-10-09
3             4            5      M   41         40 1956-12-01
4             5            5      F   37         30 1960-07-03
...         ...          ...    ...  ...        ...        ...
5364      13955            1      F   52         50 1945-10-30
5365      13956            1      M   54         50 1943-04-06
5366      13968           61      M   29         20 1968-04-13
5367      13971           67      F   35         30 1962-10-19
5368      13998           74      F   44         40 1953-08-12

[5369 rows x 6 columns]

In [501]:
client_disp = pd.merge(client, disp, on = 'client_id', how = 'left')

In [575]:
client_disp['can apply loan?'] = 'Yes'
client_disp.loc[client_disp['type']== 'DISPONENT', 'can apply loan?'] = 'No'

In [576]:
client_disp

client_id  district_id gender  age  age_group birth date  disp_id  \
0             1           18      F   27         20 1970-12-13        1   
1             2            1      M   52         50 1945-02-04        2   
2             3            1      F   57         50 1940-10-09        3   
3             4            5      M   41         40 1956-12-01        4   
4             5            5      F   37         30 1960-07-03        5   
5             6           12      M   78         70 1919-09-22        6   
6             7           15      M   68         60 1929-01-25        7   
7             8           51      F   59         50 1938-02-21        8   
8             9           60      M   62         60 1935-10-16        9   
9            10           57      M   54         50 1943-05-01       10   
10           11           57      F   47         40 1950-08-22       11   
11           12           40      M   16         10 1981-02-20       12   
12           13           54      F   23         20 1974-05-29       13   
13           14           76      F   55         50 1942-06-22       14   
14           15           21      F   79         70 1918-08-28       15   
15           16           21      M   78         70 1919-02-25       16   
16           17           76      M   63         60 1934-10-13       17   
17           18           76      F   66         60 1931-04-05       18   
18           19           47      M   55         50 1942-12-28       19   
19           20           46      M   18         10 1979-01-04       20   
20           21           12      F   45         40 1952-10-29       21   
21           22            1      F   28         20 1969-10-11       22   
22           23            1      M   24         20 1973-05-29       23   
23           24           43      F   58         50 1939-07-29       24   
24           25           21      F   58         50 1939-04-23       25   
25           26           74      F   28         20 1969-04-20       26   
26           27           54      F   31         30 1966-03-26       27   
27           28            1      M   52         50 1945-09-29       28   
28           29           30      F   46         40 1951-09-11       29   
29           30           74      F   40         40 1957-10-09       30   
30           31           68      M   35         30 1962-02-09       31   
31           32           52      M   17         10 1980-07-28       32   
32           33           73      F   49         40 1948-12-04       33   
33           36            7      F   19         10 1978-07-17       36   
34           37            7      M   27         20 1970-08-10       37   
35           38           36      F   24         20 1973-07-23       38   
36           39           68      M   29         20 1968-01-25       39   
37           40            5      F   40         40 1957-01-22       40   
38           41           22      M   29         20 1968-08-27       41   
39           42           68      M   62         60 1935-08-17       42   
40           43           75      M   77         70 1920-10-28       43   
41           44           38      F   20         20 1977-01-11       44   
42           45           20      M   45         40 1952-08-26       45   
43           46           19      F   57         50 1940-01-30       46   
44           47           76      M   63         60 1934-07-14       47   
45           48           16      M   57         50 1940-02-09       48   
46           49           72      F   38         30 1959-05-11       49   
47           50           39      F   19         10 1978-07-30       50   
48           51           36      F   18         10 1979-12-02       51   
49           52           32      M   73         70 1924-12-12       52   
50           53           64      M   20         20 1977-05-05       53   
51           55           45      F   49         40 1948-09-18       55   
52           56           21   

In [545]:
loan['year'] = loan['date'].astype(str).str[0:2].astype(int)+ 1900
loan['month'] = loan['date'].astype(str).str[2:4].astype(int)
loan['day'] = loan['date'].astype(str).str[4:6].astype(int)

loan['loan date'] = loan.apply(lambda a: datetime(a['year'], a['month'], a['day']), axis = 1)
del loan['month'], loan['day']

loan_1997 = loan[loan['year'] == 1997]
loan_1997 = loan_1997.reset_index()



In [547]:
del loan_1997['index'], loan_1997['date'], loan_1997['duration'], loan_1997['status'], loan_1997['loan date'], loan_1997['year'], loan_1997['payments']

In [554]:
loan_1997['loan granted'] = 1

In [555]:
loan_1997.head()

loan_id  account_id  amount  loan granted
0     5895        4473   93960             1
1     7122       10365  260640             1
2     6173        5724  232560             1
3     6142        5591  221880             1
4     5358        2018   38520             1

In [544]:
loan

loan_id  account_id    date  amount  duration  payments status
0       5314        1787  930705   96396        12    8033.0      B
1       5316        1801  930711  165960        36    4610.0      A
2       6863        9188  930728  127080        60    2118.0      A
3       5325        1843  930803  105804        36    2939.0      A
4       7240       11013  930906  274740        60    4579.0      A
5       6687        8261  930913   87840        24    3660.0      A
6       7284       11265  930915   52788        12    4399.0      A
7       6111        5428  930924  174744        24    7281.0      B
8       7235       10973  931013  154416        48    3217.0      A
9       5997        4894  931104  117024        24    4876.0      A
10      7121       10364  931110   21924        36     609.0      A
11      6077        5270  931122   79608        24    3317.0      A
12      6228        6034  931201  464520        60    7742.0      B
13      6356        6701  931208   95400        36    2650.0      A
14      5523        2705  931208   93888        36    2608.0      A
15      6456        7123  931209   47016        12    3918.0      A
16      7104       10320  931213  259740        60    4329.0      A
17      6820        9034  931216   38148        12    3179.0      A
18      6876        9236  931221   86616        12    7218.0      A
19      7097       10266  931223   75624        24    3151.0      B
20      4959           2  940105   80952        24    3373.0      A
21      6499        7401  940105   80952        24    3373.0      A
22      5479        2486  940110   24516        12    2043.0      A
23      5170        1071  940120  253200        60    4220.0      C
24      6721        8475  940121   21072        24     878.0      A
25      7259       11111  940131  108144        36    3004.0      A
26      5285        1603  940206   78936        12    6578.0      A
27      5189        1166  940207  149040        48    3105.0      A
28      6650        8073  940217   49320        12    4110.0      B
29      7226       10940  940223  197748        36    5493.0      A
30      6087        5313  940227  300660        60    5011.0      C
31      7262       11135  940301  182628        36    5073.0      A
32      5519        2694  940308   91632        12    7636.0      A
33      6577        7753  940311   51696        24    2154.0      A
34      6509        7445  940315   55368        24    2307.0      A
35      6520        7485  940316   91200        24    3800.0      A
36      6699        8330  940330    7656        24     319.0      A
37      6336        6555  940331  212400        36    5900.0      A
38      7055       10079  940406  167100        60    2785.0      C
39      6103        5385  940407  149340        60    2489.0      C
40      6202        5891  940418   65184        12    5432.0      A
41      7066       10131  940502  215388        36    5983.0      B
42      6696        8321  940509   89040        60    1484.0      C
43      6072        5256  940510  193968        36    5388.0      A
44      5130         813  940511   24312        12    2026.0      A
45      5568        2933  940517  272520        60    4542.0      C
46      6678        8173  940520   80340        12    6695.0      A
47      6998        9833  940521   97632        12    8136.0      A
48      6580        7769  940522  196080        48    4085.0      A
49      6316        6473  940526   76908        12    6409.0      B
50      6512        7454  940526   63312        48    1319.0      A
51      6407        6930  940526   25944        24    1081.0      A
52      5002         173  940531  104808        12    8734.0      A
53      6647        8051  940601  208320        48    4340.0      A
54      7137       10439  940603  151560        24    6315.0      A
55      6903        9337  940604   52128        24    2172.0      A
56      5918        4576  940604  300204        36    8339.0      A
57      6642        8027  940605   77640        12    6470.0 

In [530]:
card['year'] = card['issued'].astype(str).str[0:2].astype(int)+ 1900
card['month'] = card['issued'].astype(str).str[2:4].astype(int)
card['day'] = card['issued'].astype(str).str[4:6].astype(int)

card['Card Issued Date'] = card.apply(lambda a: datetime(a['year'], a['month'], a['day']), axis = 1)

card_1997 = card[card['year'] == 1997 ]
card_1997 = card_1997.reset_index()

In [534]:
del card_1997['month'], card_1997['day'], card_1997['index']

In [536]:
card_1997['Card Issued'] = 1

In [541]:
del card_1997['issued'], card_1997['year'], card_1997['Card Issued Date']

In [543]:
card_1997

card_id  disp_id     type  Issued_0/1
0       1118    11393  classic           1
1        175     1040  classic           1
2        565     3601     gold           1
3        714     4638  classic           1
4        137      786   junior           1
5         22      138  classic           1
6        325     2102  classic           1
7        194     1182  classic           1
8        668     4340  classic           1
9        706     4559     gold           1
10       850     6644  classic           1
11       298     1885  classic           1
12       105      590  classic           1
13      1036     9735  classic           1
14       292     1842     gold           1
15       112      626   junior           1
16       678     4405     gold           1
17      1093    11011  classic           1
18       681     4426  classic           1
19       582     3733  classic           1
20       729     4740   junior           1
21        54      334  classic           1
22       258     1607  classic           1
23       534     3387  classic           1
24       667     4333  classic           1
25       195     1194  classic           1
26       199     1213  classic           1
27       490     3136     gold           1
28       347     2184  classic           1
29       210     1253  classic           1
30       293     1850  classic           1
31       189     1157  classic           1
32       324     2074  classic           1
33       578     3689   junior           1
34       266     1690  classic           1
35       568     3615  classic           1
36       171     1027  classic           1
37       679     4416  classic           1
38       841     6468  classic           1
39       513     3260  classic           1
40       647     4171   junior           1
41       665     4318  classic           1
42       400     2529  classic           1
43       617     3944     gold           1
44       709     4587   junior           1
45       387     2481  classic           1
46       226     1378  classic           1
47       350     2226  classic           1
48       539     3415  classic           1
49       583     3735  classic           1
50       576     3671  classic           1
51       232     1396  classic           1
52       730     4749  classic           1
53       616     3943  classic           1
54       564     3590  classic           1
55        82      474  classic           1
56      1173    12442  classic           1
57       426     2686  classic           1
58       791     5521  classic           1
59       572     3636   junior           1
60       375     2425   junior           1
61        69      438  classic           1
62       607     3885  classic           1
63       155      900   junior           1
64       275     1762  classic           1
65       847     6610  classic           1
66       399     2527  classic           1
67       305     1914  classic           1
68       430     2713  classic           1
69       349     2214  classic           1
70       256     1583  classic           1
71        50      309  classic           1
72       939     8217   junior           1
73       110      608  classic           1
74       184     1089     gold           1
75        90      503  classic           1
76       597     3813   junior           1
77       471     3037  classic           1
78       494     3173  classic           1
79       211     1271  classic           1
80       353     2259  classic           1
81       213     1289     gold           1
82      1009     9409     gold           1
83       297     1883  classic           1
84       801     5684  classic           1
85       748     4923  classic           1
86       133      742  classic           1
87       316     2013  classic           1
88       145      819  classic           1
89       270     1736   junior           1
90      1178    12542  classic           1
91       222     1345  classic           1
92    

In [494]:
account.isna().sum().sum()

0

In [573]:
account['open year'] = account['date'].astype(str).str[0:2].astype(int) + 1900
account['open month'] = account['date'].astype(str).str[2:4].astype(int)
account['day'] = account['date'].astype(str).str[4:6].astype(int)
account['open_date'] = account.apply(lambda a: datetime(a['open year'], a['open month'], a['day']), axis = 1)
account['LOR'] = 1996 - account['open year']

account = account[account['open year'] < 1997]

account['frequency'] = account['frequency'].map({'POPLATEK MESICNE':'Monthly Issuance',
                                                'POPLATEK TYDNE': 'Weekly Issuance',
                                                'POPLATEK PO OBRATU': 'Issuance after transaction'})



del account['date'], account['open month'], account['day'], account['open year'], account['open_date']



In [574]:
account

account_id  district_id                   frequency  LOR
0            576           55            Monthly Issuance    3
1           3818           74            Monthly Issuance    3
2            704           55            Monthly Issuance    3
3           2378           16            Monthly Issuance    3
4           2632           24            Monthly Issuance    3
5           1972           77            Monthly Issuance    3
6           1539            1  Issuance after transaction    3
7            793           47            Monthly Issuance    3
8           2484           74            Monthly Issuance    3
9           1695           76            Monthly Issuance    3
10          1726           48            Monthly Issuance    3
11          2881           70            Monthly Issuance    3
12          2357           19            Monthly Issuance    3
13          2177           62            Monthly Issuance    3
14           485            6  Issuance after transaction    3
15           652           21            Monthly Issuance    3
16          9635           70            Monthly Issuance    3
17          1844           44            Monthly Issuance    3
18          1926           37            Monthly Issuance    3
19          2393           10            Monthly Issuance    3
20          3510           41            Monthly Issuance    3
21          1276           36            Monthly Issuance    3
22          1637            1            Monthly Issuance    3
23          3871           26            Monthly Issuance    3
24           192           55            Monthly Issuance    3
25           764            1            Monthly Issuance    3
26          2087            7             Weekly Issuance    3
27          2122           68            Monthly Issuance    3
28          3592           54            Monthly Issuance    3
29          3487           41            Monthly Issuance    3
30           435           38            Monthly Issuance    3
31          1730            1            Monthly Issuance    3
32          1493           41            Monthly Issuance    3
33           374           38            Monthly Issuance    3
34          2925            1            Monthly Issuance    3
35           866            9            Monthly Issuance    3
36          1628           60            Monthly Issuance    3
37          2379           44            Monthly Issuance    3
38          1979           26            Monthly Issuance    3
39           346           37            Monthly Issuance    3
40          1338           74            Monthly Issuance    3
41          1909           14            Monthly Issuance    3
42          2099            3             Weekly Issuance    3
43          3760           44            Monthly Issuance    3
44          5270           44            Monthly Issuance    3
45          1699           53            Monthly Issuance    3
46          3909            1            Monthly Issuance    3
47          2926           50            Monthly Issuance    3
48          1731           33            Monthly Issuance    3
49         11265           15            Monthly Issuance    3
50          2519            4            Monthly Issuance    3
51         10364           55            Monthly Issuance    3
52          1481           15            Monthly Issuance    3
53           401           32            Monthly Issuance    3
54          4034            1            Monthly Issuance    3
55          2330           54            Monthly Issuance    3
56          1806           40            Monthly Issuance    3
57          3834           54            Monthly Issuance    3
58          1222           66            Monthly Issuance    3
59           212           27             Weekly Issuance    3
60           456           49            Monthly Issuance    3
61           459           47            Monthly Issuance    3
62           772           45        

In [562]:
del account['open year']

In [563]:
account = account[account['open year'] < 1996]

KeyError: 'open year'

In [556]:
account['frequency'] = account['frequency'].map({'POPLATEK MESICNE':'Monthly Issuance',
                                                'POPLATEK TYDNE': 'Weekly Issuance',
                                                'POPLATEK PO OBRATU': 'Issuance after transaction'})

In [557]:
account.sort_values('account_id')

account_id  district_id                   frequency    date
1720           1           18            Monthly Issuance  950324
182            2            1            Monthly Issuance  930226
4072           3            5            Monthly Issuance  970707
2426           4           12            Monthly Issuance  960221
3976           5           15            Monthly Issuance  970530
1465           6           51            Monthly Issuance  940927
3462           7           60            Monthly Issuance  961124
2047           8           57            Monthly Issuance  950921
86             9           70            Monthly Issuance  930127
3130          10           54            Monthly Issuance  960828
2080          11           76            Monthly Issuance  951010
3852          12           21            Monthly Issuance  970415
4182          13           76            Monthly Issuance  970817
3470          14           47            Monthly Issuance  961127
858           15           70            Monthly Issuance  931002
4275          16           12            Monthly Issuance  970923
3617          17            1            Monthly Issuance  970108
457           18           43             Weekly Issuance  930526
1749          19           21            Monthly Issuance  950407
3113          20           74            Monthly Issuance  960824
4442          21           54            Monthly Issuance  971206
1221          22            1            Monthly Issuance  940323
440           23           30            Monthly Issuance  930522
3499          24           74            Monthly Issuance  961205
3008          25           68            Monthly Issuance  960728
683           26           52            Monthly Issuance  930808
850           27           73            Monthly Issuance  930926
1536          29            7            Monthly Issuance  941124
1695          30           36            Monthly Issuance  950304
1263          31           68            Monthly Issuance  940427
1990          32            5            Monthly Issuance  950828
743           33           22            Monthly Issuance  930826
822           34           67             Weekly Issuance  930917
578           35           75            Monthly Issuance  930707
557           36            1            Monthly Issuance  930701
4184          37           20            Monthly Issuance  970818
4158          38           19             Weekly Issuance  970808
836           39           36            Monthly Issuance  930922
922           40           64            Monthly Issuance  931025
4134          41           72            Monthly Issuance  970802
3079          42           39            Monthly Issuance  960816
1346          43           36            Monthly Issuance  940612
404           44           32            Monthly Issuance  930510
4216          45           64            Monthly Issuance  970902
688           47           45            Monthly Issuance  930808
3426          48           21            Monthly Issuance  961117
3823          49            1            Monthly Issuance  970406
1285          50            1            Monthly Issuance  940506
2710          51           67            Monthly Issuance  960511
3664          52           16            Monthly Issuance  970129
1847          53           77            Monthly Issuance  950607
1787          54            4            Monthly Issuance  950502
2418          55           20            Monthly Issuance  960219
1300          56           50            Monthly Issuance  940516
1822          57            1            Monthly Issuance  950521
3108          58           29            Monthly Issuance  960823
1225          59           43            Monthly Issuance  940327
1082          61           70            Monthly Issuance  931211
287           62           47            Monthly Issuance  930328
3420          63           22            Month

In [302]:
card.isna().sum().sum()
card.dtypes

card_id     int64
disp_id     int64
type       object
issued     object
dtype: object

In [304]:
card['issued_year'] = card['issued'].astype(str).str[0:2].astype(int) + 1900
card['month'] = card['issued'].astype(str).str[2:4].astype(int)
card['day'] = card['issued'].astype(str).str[4:6].astype(int)
card['issued_date'] = card.apply(lambda a: datetime(a['issued_year'], a['month'], a['day']), axis = 1)

In [305]:
del card['issued'], card['month'], card['day']
card.head()

card_id  disp_id     type  issued_year issued_date
0     1005     9285  classic         1993  1993-11-07
1      104      588  classic         1994  1994-01-19
2      747     4915  classic         1994  1994-02-05
3       70      439  classic         1994  1994-02-08
4      577     3687  classic         1994  1994-02-15

In [306]:
disp.head()

disp_id  client_id  account_id       type
0        1          1           1      OWNER
1        2          2           2      OWNER
2        3          3           2  DISPONENT
3        4          4           3      OWNER
4        5          5           3  DISPONENT

In [307]:
card_details = pd.merge(card, disp, on = 'disp_id')

In [308]:
card_details.head()

card_id  disp_id   type_x  issued_year issued_date  client_id  account_id  \
0     1005     9285  classic         1993  1993-11-07       9593        7753   
1      104      588  classic         1994  1994-01-19        588         489   
2      747     4915  classic         1994  1994-02-05       4915        4078   
3       70      439  classic         1994  1994-02-08        439         361   
4      577     3687  classic         1994  1994-02-15       3687        3050   

  type_y  
0  OWNER  
1  OWNER  
2  OWNER  
3  OWNER  
4  OWNER

In [28]:
district.head()

A1           A2               A3       A4  A5  A6  A7  A8  A9    A10  \
0   1  Hl.m. Praha           Prague  1204953   0   0   0   1   1  100.0   
1   2      Benesov  central Bohemia    88884  80  26   6   2   5   46.7   
2   3       Beroun  central Bohemia    75232  55  26   4   1   5   41.7   
3   4       Kladno  central Bohemia   149893  63  29   6   2   6   67.4   
4   5        Kolin  central Bohemia    95616  65  30   4   1   6   51.4   

     A11   A12   A13  A14    A15    A16  
0  12541  0.29  0.43  167  85677  99107  
1   8507  1.67  1.85  132   2159   2674  
2   8980  1.95  2.21  111   2824   2813  
3   9753  4.64  5.05  109   5244   5892  
4   9307  3.85  4.43  118   2616   3040

In [29]:
district.isna().sum().sum()

0

In [30]:
district  = district.rename(columns = {'A1': 'district_id', 
                                       'A2':'district name',
                                       'A3': 'region',
                                       'A4': 'inhabitants',
                                       'A5': 'municipalities with inhabitants < 499',
                                       'A6': 'municipalities with inhabitants 500-1999',
                                       'A7': 'municipalities with inhabitants 2000-9999',
                                       'A8': 'municipalities with inhabitants >10000',
                                       'A9': 'cities',
                                       'A10': 'ratio of urban inhabitants',
                                       'A11': 'average salary',
                                       'A12': 'unemploymant rate 1995',
                                       'A13': 'unemploymant rate 1996',
                                       'A14': 'enterpreneurs per 1000 inhabitants',
                                       'A15': 'commited crimes 1995',
                                       'A16': 'commited crimes 1996'})
district.head()                                             

district_id district name           region  inhabitants  \
0            1   Hl.m. Praha           Prague      1204953   
1            2       Benesov  central Bohemia        88884   
2            3        Beroun  central Bohemia        75232   
3            4        Kladno  central Bohemia       149893   
4            5         Kolin  central Bohemia        95616   

   municipalities with inhabitants < 499  \
0                                      0   
1                                     80   
2                                     55   
3                                     63   
4                                     65   

   municipalities with inhabitants 500-1999  \
0                                         0   
1                                        26   
2                                        26   
3                                        29   
4                                        30   

   municipalities with inhabitants 2000-9999  \
0                                          0   
1                                          6   
2                                          4   
3                                          6   
4                                          4   

   municipalities with inhabitants >10000  cities  ratio of urban inhabitants  \
0                                       1       1                       100.0   
1                                       2       5                        46.7   
2                                       1       5                        41.7   
3                                       2       6                        67.4   
4                                       1       6                        51.4   

   average salary unemploymant rate 1995  unemploymant rate 1996  \
0           12541                   0.29                    0.43   
1            8507                   1.67                    1.85   
2            8980                   1.95                    2.21   
3            9753                   4.64                    5.05   
4            9307                   3.85                    4.43   

   enterpreneurs per 1000 inhabitants commited crimes 1995  \
0                                 167                85677   
1                                 132                 2159   
2                                 111                 2824   
3                                 109                 5244   
4                                 118                 2616   

   commited crimes 1996  
0                 99107  
1                  2674  
2                  2813  
3                  5892  
4                  3040

In [32]:
disp.head()


disp_id  client_id  account_id       type
0        1          1           1      OWNER
1        2          2           2      OWNER
2        3          3           2  DISPONENT
3        4          4           3      OWNER
4        5          5           3  DISPONENT

In [82]:
order['k_symbol'].unique()

array(['SIPO', 'UVER', ' ', 'POJISTNE', 'LEASING'], dtype=object)

In [539]:
order.head()

order_id  account_id bank_to  account_to  amount k_symbol
0     29401           1      YZ    87144583  2452.0     SIPO
1     29402           2      ST    89597016  3372.7     UVER
2     29403           2      QR    13943797  7266.0     SIPO
3     29404           3      WX    83084338  1135.0     SIPO
4     29405           3      CD    24485939   327.0

In [540]:
order['k_symbol'] = order['k_symbol'].map({
    'SIPO' : 'household payment',
    'UVER' : 'loan payment', ' ': 'other', 'POJISTNE' : 'insurance payment', 'LEASING': 'lease'
})

In [159]:
order[order['account_id']== 3]

order_id  account_id bank_to  account_to  amount           k_symbol
3     29404           3      WX    83084338  1135.0  household payment
4     29405           3      CD    24485939   327.0              other
5     29406           3      AB    59972357  3539.0  insurance payment

In [160]:
order = order.pivot_table(index=['account_id'], columns = 'k_symbol', values = 'amount', fill_value = 0)
order.columns.name = None

In [100]:
order = order.reset_index()

In [101]:
order.head()

account_id  household payment  insurance payment  lease  loan payment  \
0           1             2452.0                  0    0.0           0.0   
1           2             7266.0                  0    0.0        3372.7   
2           3             1135.0               3539    0.0           0.0   
3           4             1681.5                  0    0.0           0.0   
4           5             2668.0                  0    0.0           0.0   

   other  
0    0.0  
1    0.0  
2  327.0  
3    0.0  
4    0.0

In [104]:
order['total order payment'] = order['household payment']+order['lease']+order['other']+order['loan payment'] + order['insurance payment']
order.head()

account_id  household payment  insurance payment  lease  loan payment  \
0           1             2452.0                  0    0.0           0.0   
1           2             7266.0                  0    0.0        3372.7   
2           3             1135.0               3539    0.0           0.0   
3           4             1681.5                  0    0.0           0.0   
4           5             2668.0                  0    0.0           0.0   

   other  total order payment  
0    0.0               2452.0  
1    0.0              10638.7  
2  327.0               5001.0  
3    0.0               1681.5  
4    0.0               2668.0

In [94]:
trans.head()

trans_id  account_id    date    type operation  amount  balance k_symbol  \
0    695247        2378  930101  PRIJEM     VKLAD   700.0    700.0      NaN   
1    171812         576  930101  PRIJEM     VKLAD   900.0    900.0      NaN   
2    207264         704  930101  PRIJEM     VKLAD  1000.0   1000.0      NaN   
3   1117247        3818  930101  PRIJEM     VKLAD   600.0    600.0      NaN   
4    579373        1972  930102  PRIJEM     VKLAD   400.0    400.0      NaN   

  bank  account  
0  NaN      NaN  
1  NaN      NaN  
2  NaN      NaN  
3  NaN      NaN  
4  NaN      NaN

In [95]:
trans['operation'].unique()

array(['VKLAD', 'PREVOD Z UCTU', 'VYBER', nan, 'PREVOD NA UCET',
       'VYBER KARTOU'], dtype=object)

In [96]:
trans['type'].unique()

array(['PRIJEM', 'VYDAJ', 'VYBER'], dtype=object)

In [97]:
trans['k_symbol'].unique()

array([nan, 'DUCHOD', 'UROK', 'SIPO', 'SLUZBY', ' ', 'POJISTNE',
       'SANKC. UROK', 'UVER'], dtype=object)

In [98]:
trans['bank'].unique()

array([nan, 'YZ', 'IJ', 'ST', 'UV', 'MN', 'OP', 'AB', 'CD', 'WX', 'GH',
       'EF', 'QR', 'KL'], dtype=object)

In [99]:
trans['account'].unique()

array([      nan, 62457513.,  6149286., ..., 63637012., 66904526.,
       74396675.])

In [436]:
trans['year'] = trans['date'].astype(str).str[0:2].astype(int) + 1900
trans['month'] = trans['date'].astype(str).str[2:4].astype(int)
trans['day'] = trans['date'].astype(str).str[4:6].astype(int) 
trans['transaction_date'] = trans.apply(lambda a: datetime(a['year'], a['month'], a['day']), axis = 1)

In [437]:
del trans['date']

In [438]:
trans_balance = trans[['account_id', 'year', 'month', 'day', 'balance']]

In [439]:
trans_balance = trans_balance.sort_values(['account_id', 'year', 'month', 'day'], ascending = [True, True, True, False])

In [440]:
trans_balance

account_id  year  month  day  balance
149431            1  1995      3   24   1000.0
162680            1  1995      4   30  17298.2
158831            1  1995      4   23  17279.0
157403            1  1995      4   13   4679.0
172578            1  1995      5   31  23156.2
...             ...   ...    ...  ...      ...
1053036       11382  1998     12   31  81373.6
1056161       11382  1998     12   31  81674.7
1050361       11382  1998     12   25  81062.4
1040573       11382  1998     12   10  87362.4
1033140       11382  1998     12    2  41114.4

[1056320 rows x 5 columns]

In [441]:
def FindMonthEnd(df):
    df1 = pd.Series(0, index=df.index)
    df1.iloc[-1] = 1
    return df1

trans_balance["Month end"] = trans_balance.groupby(['account_id','year', 'month'])['day'].apply(FindMonthEnd)


In [442]:
trans_balance = trans_balance[trans_balance['Month end'] == 1]

In [443]:
trans_balance = trans_balance[trans_balance['year'] == 1996]

In [444]:
del trans_balance['year'], trans_balance['month'], trans_balance['day'], trans_balance['Month end']

In [445]:
trans_balance = trans_balance.groupby('account_id').agg( {'balance':['mean', 'median']}) 

In [449]:
trans_balance.columns = ['Average Montly Balance', 'Median Monthly Balance']

In [450]:
trans_balance.columns.name = None
trans_balance = trans_balance.reset_index()

In [451]:
trans_balance

account_id  Average Montly Balance  Median Monthly Balance
0              1            14348.100000                14134.60
1              2            30335.083333                30212.25
2              4            18304.381818                21534.70
3              6            31743.675000                32696.55
4              7            17887.500000                17887.50
...          ...                     ...                     ...
3597       11333            44832.516667                37900.40
3598       11349            75088.391667                78400.90
3599       11359            23923.100000                22945.30
3600       11362            37592.058333                39864.10
3601       11382            52328.358333                55759.35

[3602 rows x 3 columns]

In [360]:
trans['operation'] = trans['operation'].map({
    'VKLAD': 'Credit in Cash', 'PREVOD Z UCTU': 'Collection from another bank' , 'VYBER':'withdrawal in cash', 
    'PREVOD NA UCET': 'remittance to another bank',
       'VYBER KARTOU': 'remittance to another bank',
})

In [361]:
trans.loc[trans['operation'].isna(), 'operation'] = 'Interest Credited'

In [362]:
trans = trans.pivot_table(index = ['account_id', 'transaction_date', 'balance', 'month', 'year'], columns = 'operation', 
                          values = 'amount', fill_value = 0)

In [363]:
trans.columns.name = None
trans = trans.reset_index()

In [364]:
trans.head(20)

account_id transaction_date  balance  month  year  \
0            1       1995-03-24   1000.0      3  1995   
1            1       1995-04-13   4679.0      4  1995   
2            1       1995-04-23  17279.0      4  1995   
3            1       1995-04-30  17298.2      4  1995   
4            1       1995-05-13  20977.2      5  1995   
5            1       1995-05-23  23077.2      5  1995   
6            1       1995-05-31  23156.2      5  1995   
7            1       1995-06-13  26835.2      6  1995   
8            1       1995-06-22  26635.2      6  1995   
9            1       1995-06-30  26735.8      6  1995   
10           1       1995-07-13  30414.8      7  1995   
11           1       1995-07-22  25114.8      7  1995   
12           1       1995-07-31  25223.7      7  1995   
13           1       1995-08-13  28902.7      8  1995   
14           1       1995-08-21  21402.7      8  1995   
15           1       1995-08-31  21487.3      8  1995   
16           1       1995-08-31  21501.9      8  1995   
17           1       1995-09-05  19035.3      9  1995   
18           1       1995-09-13  22714.3      9  1995   
19           1       1995-09-20  22014.3      9  1995   

    Collection from another bank  Credit in Cash  Interest Credited  \
0                              0          1000.0                0.0   
1                           3679             0.0                0.0   
2                              0         12600.0                0.0   
3                              0             0.0               19.2   
4                           3679             0.0                0.0   
5                              0          2100.0                0.0   
6                              0             0.0               79.0   
7                           3679             0.0                0.0   
8                              0             0.0                0.0   
9                              0             0.0              100.6   
10                          3679             0.0                0.0   
11                             0             0.0                0.0   
12                             0             0.0              108.9   
13                          3679             0.0                0.0   
14                             0             0.0                0.0   
15                             0             0.0                0.0   
16                             0             0.0               99.2   
17                             0             0.0                0.0   
18                          3679             0.0                0.0   
19                             0             0.0                0.0   

    remittance to another bank  withdrawal in cash  
0                          0.0                 0.0  
1                          0.0                 0.0  
2                          0.0                 0.0  
3                          0.0                 0.0  
4                          0.0                 0.0  
5                          0.0                 0.0  
6                          0.0                 0.0  
7                          0.0                 0.0  
8                          0.0               200.0  
9                          0.0                 0.0  
10                         0.0                 0.0  
11                         0.0              5300.0  
12                         0.0                 0.0  
13                         0.0                 0.0  
14                         0.0              7500.0  
15                         0.0                14.6  
16                         0.0                 0.0  
17                      2452.0                 0.0  
18                         0.0                 0.0  
19                         0.0               700.0

In [365]:
trans_96 = trans[trans['year'] == 1996]
del trans_96['year'], trans_96['balance']

In [366]:
trans_96.head(10)

account_id transaction_date  month  Collection from another bank  \
39           1       1996-01-04      1                             0   
40           1       1996-01-05      1                             0   
41           1       1996-01-09      1                             0   
42           1       1996-01-09      1                             0   
43           1       1996-01-10      1                             0   
44           1       1996-01-13      1                          3679   
45           1       1996-01-18      1                             0   
46           1       1996-01-18      1                             0   
47           1       1996-01-21      1                             0   
48           1       1996-01-27      1                             0   

    Credit in Cash  Interest Credited  remittance to another bank  \
39             0.0                0.0                         0.0   
40             0.0                0.0                      2452.0   
41             0.0                0.0                         0.0   
42             0.0                0.0                         0.0   
43             0.0                0.0                         0.0   
44             0.0                0.0                         0.0   
45             0.0                0.0                         0.0   
46             0.0                0.0                         0.0   
47             0.0                0.0                         0.0   
48             0.0                0.0                         0.0   

    withdrawal in cash  
39               210.0  
40                 0.0  
41               720.0  
42               180.0  
43               420.0  
44                 0.0  
45               150.0  
46              2900.0  
47               870.0  
48               420.0

In [367]:
trans_96 = trans_96.groupby(['account_id', 'month']).agg('sum')

In [368]:
trans_96.columns.name = None
trans_96 = trans_96.reset_index()

In [374]:
trans_96['Total Credit'] = trans_96['Collection from another bank'] + trans_96['Credit in Cash'] + trans_96['Interest Credited'] 

In [373]:
trans_96.dtypes

account_id                        int64
month                             int64
Collection from another bank      int64
Credit in Cash                  float64
Interest Credited               float64
remittance to another bank      float64
withdrawal in cash              float64
Total Credit                    float64
dtype: object

In [376]:
trans_96['Total Debit'] = trans_96['remittance to another bank'] + trans_96['withdrawal in cash']

In [377]:
trans_96

account_id  month  Collection from another bank  Credit in Cash  \
0               1      1                          3679             0.0   
1               1      2                          3679           100.0   
2               1      3                          3679           200.0   
3               1      4                          3679             0.0   
4               1      5                          3679             0.0   
...           ...    ...                           ...             ...   
35488       11382      8                         30832             0.0   
35489       11382      9                         30832             0.0   
35490       11382     10                         30832             0.0   
35491       11382     11                         30832             0.0   
35492       11382     12                         46248             0.0   

       Interest Credited  remittance to another bank  withdrawal in cash  \
0                   64.1                      2452.0              5884.6   
1                   59.7                      2452.0                14.6   
2                   65.7                      2452.0                14.6   
3                   67.6                      2452.0              2014.6   
4                   63.3                      2452.0              2574.6   
...                  ...                         ...                 ...   
35488              403.4                         0.0             31683.6   
35489              252.2                         0.0             40269.6   
35490              233.3                         0.0             29023.6   
35491              200.3                         0.0             27714.6   
35492              252.8                         0.0             51814.6   

       Total Credit  Total Debit  
0            3743.1       8336.6  
1            3838.7       2466.6  
2            3944.7       2466.6  
3            3746.6       4466.6  
4            3742.3       5026.6  
...             ...          ...  
35488       31235.4      31683.6  
35489       31084.2      40269.6  
35490       31065.3      29023.6  
35491       31032.3      27714.6  
35492       46500.8      51814.6  

[35493 rows x 9 columns]

In [392]:
trans_96['monthly savings'] = trans_96['Total Credit'] - trans_96['Total Debit']

In [396]:
trans_96 = trans_96.groupby('account_id').agg('mean')

In [452]:
trans_96.columns.name = None
trans_96 = trans_96.reset_index()

In [453]:
trans_96

account_id  month  Collection from another bank  Credit in Cash  \
0              1    6.5                   3679.000000      425.000000   
1              2    6.5                  21922.333333     1958.333333   
2              4    7.0                   5048.181818       72.727273   
3              6    6.5                   6669.000000        0.000000   
4              7   11.5                      0.000000    17437.500000   
...          ...    ...                           ...             ...   
3597       11333    6.5                      0.000000    35205.916667   
3598       11349    6.5                  45487.000000      258.333333   
3599       11359    6.5                  29265.166667        0.000000   
3600       11362    6.5                      0.000000    17486.166667   
3601       11382    6.5                  33401.333333        0.000000   

      Interest Credited  remittance to another bank  withdrawal in cash  \
0             68.166667                 2452.000000         2179.600000   
1            164.575000                 7266.000000        15615.183333   
2             53.681818                 1645.454545         1261.600000   
3            123.308333                 3954.000000         2862.933333   
4             15.200000                    0.000000         3300.000000   
...                 ...                         ...                 ...   
3597         296.375000                    0.000000        33991.866667   
3598         193.941667                17884.000000        27340.083333   
3599         132.916667                 7672.958333        21645.100000   
3600         115.633333                 4412.500000        14117.166667   
3601         222.058333                    0.000000        36195.083333   

      Total Credit   Total Debit  monthly savings  
0      4172.166667   4631.600000      -459.433333  
1     24045.241667  22881.183333      1164.058333  
2      5174.590909   2907.054545      2267.536364  
3      6792.308333   6816.933333       -24.625000  
4     17452.700000   3300.000000     14152.700000  
...            ...           ...              ...  
3597  35502.291667  33991.866667      1510.425000  
3598  45939.275000  45224.083333       715.191667  
3599  29398.083333  29318.058333        80.025000  
3600  17601.800000  18529.666667      -927.866667  
3601  33623.391667  36195.083333     -2571.691667  

[3602 rows x 10 columns]

In [454]:
trans_96.columns

Index(['account_id', 'month', 'Collection from another bank', 'Credit in Cash',
       'Interest Credited', 'remittance to another bank', 'withdrawal in cash',
       'Total Credit', 'Total Debit', 'monthly savings'],
      dtype='object')

In [455]:
trans_96 = trans_96.rename(columns = {'Collection from another bank': 'Average Collection from another bank' , 
                                      'Credit in Cash' : 'Average Credit in Cash' ,
                                      'Interest Credited':'Average Interest Credited', 
                                      'remittance to another bank' : ' Average remittance to another bank' ,
                                      'withdrawal in cash': 'Average withdrawal in cash',
                                      'Total Credit' : 'Average Total Credit', 
                                      'Total Debit' : 'Average Total Debit', 
                                      'monthly savings': 'Average Monthly Savings'})

In [456]:
trans_96

account_id  month  Average Collection from another bank  \
0              1    6.5                           3679.000000   
1              2    6.5                          21922.333333   
2              4    7.0                           5048.181818   
3              6    6.5                           6669.000000   
4              7   11.5                              0.000000   
...          ...    ...                                   ...   
3597       11333    6.5                              0.000000   
3598       11349    6.5                          45487.000000   
3599       11359    6.5                          29265.166667   
3600       11362    6.5                              0.000000   
3601       11382    6.5                          33401.333333   

      Average Credit in Cash  Average Interest Credited  \
0                 425.000000                  68.166667   
1                1958.333333                 164.575000   
2                  72.727273                  53.681818   
3                   0.000000                 123.308333   
4               17437.500000                  15.200000   
...                      ...                        ...   
3597            35205.916667                 296.375000   
3598              258.333333                 193.941667   
3599                0.000000                 132.916667   
3600            17486.166667                 115.633333   
3601                0.000000                 222.058333   

       Average remittance to another bank  Average withdrawal in cash  \
0                             2452.000000                 2179.600000   
1                             7266.000000                15615.183333   
2                             1645.454545                 1261.600000   
3                             3954.000000                 2862.933333   
4                                0.000000                 3300.000000   
...                                   ...                         ...   
3597                             0.000000                33991.866667   
3598                         17884.000000                27340.083333   
3599                          7672.958333                21645.100000   
3600                          4412.500000                14117.166667   
3601                             0.000000                36195.083333   

      Average Total Credit  Average Total Debit  Average Monthly Savings  
0              4172.166667          4631.600000              -459.433333  
1             24045.241667         22881.183333              1164.058333  
2              5174.590909          2907.054545              2267.536364  
3              6792.308333          6816.933333               -24.625000  
4             17452.700000          3300.000000             14152.700000  
...                    ...                  ...                      ...  
3597          35502.291667         33991.866667              1510.425000  
3598          45939.275000         45224.083333               715.191667  
3599          29398.083333         29318.058333                80.025000  
3600          17601.800000         18529.666667              -927.866667  
3601          33623.391667         36195.083333             -2571.691667  

[3602 rows x 10 columns]

In [457]:
transaction_summary = pd.merge(trans_96, trans_balance, on = 'account_id')

In [460]:
transaction_summary

account_id  month  Average Collection from another bank  \
0              1    6.5                           3679.000000   
1              2    6.5                          21922.333333   
2              4    7.0                           5048.181818   
3              6    6.5                           6669.000000   
4              7   11.5                              0.000000   
...          ...    ...                                   ...   
3597       11333    6.5                              0.000000   
3598       11349    6.5                          45487.000000   
3599       11359    6.5                          29265.166667   
3600       11362    6.5                              0.000000   
3601       11382    6.5                          33401.333333   

      Average Credit in Cash  Average Interest Credited  \
0                 425.000000                  68.166667   
1                1958.333333                 164.575000   
2                  72.727273                  53.681818   
3                   0.000000                 123.308333   
4               17437.500000                  15.200000   
...                      ...                        ...   
3597            35205.916667                 296.375000   
3598              258.333333                 193.941667   
3599                0.000000                 132.916667   
3600            17486.166667                 115.633333   
3601                0.000000                 222.058333   

       Average remittance to another bank  Average withdrawal in cash  \
0                             2452.000000                 2179.600000   
1                             7266.000000                15615.183333   
2                             1645.454545                 1261.600000   
3                             3954.000000                 2862.933333   
4                                0.000000                 3300.000000   
...                                   ...                         ...   
3597                             0.000000                33991.866667   
3598                         17884.000000                27340.083333   
3599                          7672.958333                21645.100000   
3600                          4412.500000                14117.166667   
3601                             0.000000                36195.083333   

      Average Total Credit  Average Total Debit  Average Monthly Savings  \
0              4172.166667          4631.600000              -459.433333   
1             24045.241667         22881.183333              1164.058333   
2              5174.590909          2907.054545              2267.536364   
3              6792.308333          6816.933333               -24.625000   
4             17452.700000          3300.000000             14152.700000   
...                    ...                  ...                      ...   
3597          35502.291667         33991.866667              1510.425000   
3598          45939.275000         45224.083333               715.191667   
3599          29398.083333         29318.058333                80.025000   
3600          17601.800000         18529.666667              -927.866667   
3601          33623.391667         36195.083333             -2571.691667   

      Average Montly Balance  Median Monthly Balance  
0               14348.100000                14134.60  
1               30335.083333                30212.25  
2               18304.381818                21534.70  
3               31743.675000                32696.55  
4               17887.500000                17887.50  
...                      ...                     ...  
3597            44832.516667                37900.40  
3598            75088.391667                78400.90  
3599            23923.100000                22945.30  
3600            37592.058333                39864.10  
3601            52328.358333                55759.35  

[3602 rows x 12 columns]

In [461]:
del transaction_summary['month']

In [462]:
transaction_summary

account_id  Average Collection from another bank  \
0              1                           3679.000000   
1              2                          21922.333333   
2              4                           5048.181818   
3              6                           6669.000000   
4              7                              0.000000   
...          ...                                   ...   
3597       11333                              0.000000   
3598       11349                          45487.000000   
3599       11359                          29265.166667   
3600       11362                              0.000000   
3601       11382                          33401.333333   

      Average Credit in Cash  Average Interest Credited  \
0                 425.000000                  68.166667   
1                1958.333333                 164.575000   
2                  72.727273                  53.681818   
3                   0.000000                 123.308333   
4               17437.500000                  15.200000   
...                      ...                        ...   
3597            35205.916667                 296.375000   
3598              258.333333                 193.941667   
3599                0.000000                 132.916667   
3600            17486.166667                 115.633333   
3601                0.000000                 222.058333   

       Average remittance to another bank  Average withdrawal in cash  \
0                             2452.000000                 2179.600000   
1                             7266.000000                15615.183333   
2                             1645.454545                 1261.600000   
3                             3954.000000                 2862.933333   
4                                0.000000                 3300.000000   
...                                   ...                         ...   
3597                             0.000000                33991.866667   
3598                         17884.000000                27340.083333   
3599                          7672.958333                21645.100000   
3600                          4412.500000                14117.166667   
3601                             0.000000                36195.083333   

      Average Total Credit  Average Total Debit  Average Monthly Savings  \
0              4172.166667          4631.600000              -459.433333   
1             24045.241667         22881.183333              1164.058333   
2              5174.590909          2907.054545              2267.536364   
3              6792.308333          6816.933333               -24.625000   
4             17452.700000          3300.000000             14152.700000   
...                    ...                  ...                      ...   
3597          35502.291667         33991.866667              1510.425000   
3598          45939.275000         45224.083333               715.191667   
3599          29398.083333         29318.058333                80.025000   
3600          17601.800000         18529.666667              -927.866667   
3601          33623.391667         36195.083333             -2571.691667   

      Average Montly Balance  Median Monthly Balance  
0               14348.100000                14134.60  
1               30335.083333                30212.25  
2               18304.381818                21534.70  
3               31743.675000                32696.55  
4               17887.500000                17887.50  
...                      ...                     ...  
3597            44832.516667                37900.40  
3598            75088.391667                78400.90  
3599            23923.100000                22945.30  
3600            37592.058333                39864.10  
3601            52328.358333                55759.35  

[3602 rows x 11 columns]

In [479]:
trans96 = trans[trans['year']==1996]

In [481]:
# Aggregate the total credit per account
trans_agg_credit = trans96[trans96['type'].isin(['PRIJEM'])].groupby('account_id')['amount'].agg('sum')
trans_agg_credit = trans_agg_credit.reset_index()
trans_agg_credit = trans_agg_credit.rename(columns={'amount':'total_credit'})
trans_agg_credit.head()

account_id  total_credit
0           1       50066.0
1           2      288542.9
2           4       56920.5
3           6       81507.7
4           7       34905.4

In [483]:
# Aggregate the total withdrawal per account
trans_agg_withdrawal = trans96[trans96['type'].isin(['VYDAJ', 'VYBER'])].groupby('account_id')['amount'].agg('sum')
trans_agg_withdrawal = trans_agg_withdrawal.reset_index()
trans_agg_withdrawal = trans_agg_withdrawal.rename(columns={'amount':'total_withdrawal'})
trans_agg_withdrawal.head()

account_id  total_withdrawal
0           1           55579.2
1           2          274574.2
2           4           31977.6
3           6           81803.2
4           7            6600.0

In [484]:
transaction_summary = pd.merge(transaction_summary, trans_agg_credit, how='left', on='account_id')
transaction_summary = pd.merge(transaction_summary, trans_agg_withdrawal, how='left', on='account_id')

In [485]:
transaction_summary

account_id  Average Collection from another bank  \
0              1                           3679.000000   
1              2                          21922.333333   
2              4                           5048.181818   
3              6                           6669.000000   
4              7                              0.000000   
...          ...                                   ...   
3597       11333                              0.000000   
3598       11349                          45487.000000   
3599       11359                          29265.166667   
3600       11362                              0.000000   
3601       11382                          33401.333333   

      Average Credit in Cash  Average Interest Credited  \
0                 425.000000                  68.166667   
1                1958.333333                 164.575000   
2                  72.727273                  53.681818   
3                   0.000000                 123.308333   
4               17437.500000                  15.200000   
...                      ...                        ...   
3597            35205.916667                 296.375000   
3598              258.333333                 193.941667   
3599                0.000000                 132.916667   
3600            17486.166667                 115.633333   
3601                0.000000                 222.058333   

       Average remittance to another bank  Average withdrawal in cash  \
0                             2452.000000                 2179.600000   
1                             7266.000000                15615.183333   
2                             1645.454545                 1261.600000   
3                             3954.000000                 2862.933333   
4                                0.000000                 3300.000000   
...                                   ...                         ...   
3597                             0.000000                33991.866667   
3598                         17884.000000                27340.083333   
3599                          7672.958333                21645.100000   
3600                          4412.500000                14117.166667   
3601                             0.000000                36195.083333   

      Average Total Credit  Average Total Debit  Average Monthly Savings  \
0              4172.166667          4631.600000              -459.433333   
1             24045.241667         22881.183333              1164.058333   
2              5174.590909          2907.054545              2267.536364   
3              6792.308333          6816.933333               -24.625000   
4             17452.700000          3300.000000             14152.700000   
...                    ...                  ...                      ...   
3597          35502.291667         33991.866667              1510.425000   
3598          45939.275000         45224.083333               715.191667   
3599          29398.083333         29318.058333                80.025000   
3600          17601.800000         18529.666667              -927.866667   
3601          33623.391667         36195.083333             -2571.691667   

      Average Montly Balance  Median Monthly Balance  total_credit  \
0               14348.100000                14134.60       50066.0   
1               30335.083333                30212.25      288542.9   
2               18304.381818                21534.70       56920.5   
3               31743.675000                32696.55       81507.7   
4               17887.500000                17887.50       34905.4   
...                      ...                     ...           ...   
3597            44832.516667                37900.40      426027.5   
3598            75088.391667                78400.90      551271.3   
3599            23923.100000                22945.30      352777.0   
3600            37592.058333                39864.10      211221.6   
3601            52328.358333            